# Reptile Radar

##### The intention of this project is to give users some basic information about reptiles spotted in their area using data from the Global Biodiversity Information Facility. It concats sentences based on what animals are spotted nearby and what to look out for if those animals are potentially dangerous. 

In [18]:
# The intention of this code is to use a user's coordinates to tell them what species of animals are close to them based on a database of animal sightings.
# Import necessary libraries:
import plotly.express as px
import pandas as pd
import geopandas as gpd
from shapely.geometry import Point
import plotly.graph_objs as go
import matplotlib.pyplot as plt
%matplotlib inline
import matplotlib.pyplot as plt

df = pd.read_csv('csv/path/to/reptile/list.csv')
county_gdf = gpd.read_file('shapefile')
roads = gpd.read_file('roadshapefile.shp')
user_lon = -73.966497
user_lat = 40.665265

# Create GeoDataFrame for user point
user_point = gpd.GeoDataFrame(geometry=[Point(user_lon, user_lat)], crs="EPSG:4326")
user_point_projected = user_point.to_crs(epsg=32618)
point_gdf = gpd.GeoDataFrame(geometry=gpd.points_from_xy([user_lon], [user_lat]), crs=county_gdf.crs)

# Perform spatial join to find the county containing the user point
joined_gdf = gpd.sjoin(point_gdf, county_gdf, predicate='within')
filtered_county_gdf = county_gdf[county_gdf['NAME'] == joined_gdf['NAME'].iloc[0]]
filtered_county_gdf = filtered_county_gdf.to_crs(epsg=32618)

# Create geometry for DataFrame
geometry = [Point(lon, lat) for lon, lat in zip(df['decimallongitude'], df['decimallatitude'])]
gdf = gpd.GeoDataFrame(df, geometry=geometry, crs="EPSG:4326")
gdf = gdf.to_crs(epsg=32618)

# Define user point and create buffer around it
buffer_user_meters = 5000 
buffer = user_point_projected.buffer(buffer_user_meters)
buffer_user = buffer.to_crs(epsg=4326).__geo_interface__

#Clip the roads to the county boundary then convert to geojson
roads = roads.to_crs(epsg=32618)
clipped_roads = gpd.clip(roads, filtered_county_gdf)
clipped_roads_geojson = clipped_roads.to_crs(epsg=4326).__geo_interface__

# Create a buffer around the roads
buffer_roads_meters = 600
buffer_roads = clipped_roads.to_crs(epsg=32618).buffer(buffer_roads_meters)

# Convert the buffered roads back to GeoJSON if needed
road_buffer_geojson = buffer_roads.to_crs(epsg=4326).__geo_interface__

# Create unique color mapping for animals
unique_animals = df['animalname'].unique()
colors = px.colors.qualitative.Plotly
color_map = {animal: colors[i % len(colors)] for i, animal in enumerate(unique_animals)}
df['color2'] = df['animalname'].map(color_map)

# Initialize the figure and add the choropleth trace
fig = go.Figure()

# Create the scatter plot map using plotly.graph_objects
animal_traces = []
for animal in df['animalname'].unique():
    animal_df = df[df['animalname'] == animal]
    trace = go.Scattermapbox(
        lon=animal_df['decimallongitude'],
        lat=animal_df['decimallatitude'],
        mode='markers',
        marker=dict(size=9, color=animal_df['color2'].iloc[0]),
        text=animal_df['animalname'],
        name=animal
    )
    animal_traces.append(trace)

user_location_trace = go.Scattermapbox(
    lon=[user_lon],
    lat=[user_lat],
    marker=dict(size=20, color='red'),
    text=["You are here."],
    name='User Location',  # Adding name to ensure it appears in the legend
    showlegend=True
)

road_dummy_trace = go.Scattermapbox(
    lon=[None],
    lat=[None],
    mode='lines',
    line=dict(color='black', width=2),
    name='Roads'
)

fig.update_layout(
    mapbox=dict(
        style="open-street-map",
        zoom=12,
        center=dict(lat=user_lat, lon=user_lon),
        layers=[
            {
                "sourcetype": "geojson",
                "source": clipped_roads_geojson,
                "type": "line",
                "color": "black",
                "line": {"width": 1.5},
                "opacity": 0.7,
                "below": "traces",
            },
            {
                "sourcetype": "geojson",
                "source": road_buffer_geojson,
                "type": "fill",
                "color": "red",
                "opacity": 0.1,
                "below": "traces",
            },
            {
                "sourcetype": "geojson",
                "source": buffer_user,
                "type": "fill",
                "color": "blue",
                "opacity": 0.2,
                "below": "traces",
            }
        ]
    ),
    margin={"r":0, "t":50, "l":0, "b":10},
    width=800, 
    height=600,
    title='Reptile Radar Results',
    showlegend=True  # Ensure the legend is displayed
)

# Add the traces made earlier
for trace in animal_traces:
    fig.add_trace(trace)
    
fig.add_trace(road_dummy_trace)
fig.add_trace(user_location_trace)

intersecting_points = gdf[gdf.intersects(buffer.unary_union)]

buffer_new_union = buffer.unary_union
buffer_roads_union = buffer_roads.unary_union

intersection = buffer_new_union.intersection(buffer_roads_union)

snake_counts = df['animalname'].value_counts()
total = snake_counts.sum()
snake_percentages = snake_counts / total * 100

significant_snakes = snake_counts[snake_percentages >= 5]
significant_labels = significant_snakes.index.tolist()

#The sentences
heading = """  _____            _   _ _        _____           _            
 |  __ \          | | (_) |      |  __ \         | |           
 | |__) |___ _ __ | |_ _| | ___  | |__) |__ _  __| | __ _ _ __ 
 |  _  // _ \ '_ \| __| | |/ _ \ |  _  // _` |/ _` |/ _` | '__|
 | | \ \  __/ |_) | |_| | |  __/ | | \ \ (_| | (_| | (_| | |   
 |_|  \_\___| .__/ \__|_|_|\___| |_|  \_\__,_|\__,_|\__,_|_|   
            | |                                                
            |_|                                                """
divider = """_________________________________________________________________________"""
print(heading)
print(divider)
print()

print("Number of nearby sightings:", len(intersecting_points))
print()
unique_animals_df = intersecting_points.drop_duplicates(subset='animalname', keep='first')

# Create a GeoDataFrame for the intersection
intersection_gdf = gpd.GeoDataFrame(geometry=[intersection], crs=buffer.crs)
road_reptiles = gdf[gdf.intersects(intersection_gdf.unary_union)]
print("There are", len(road_reptiles), "reptiles near major roadways near you.")

if len(intersecting_points) > 0:
    percentage = len(road_reptiles) / len(intersecting_points) * 100
    print(f"That is {percentage:.2f}% of all sightings near you. Be mindful of their habitat.")
    print()
else:
    print("There are no sightings near roads nearby you.")
    print()

# Create a pie chart using Plotly
fig_pie = go.Figure(data=[go.Pie(labels=significant_labels, values=significant_snakes)])

# Update the layout for a smaller figure
fig_pie.update_layout(
    title='Reptiles Near Roads',
    width=600,
    height=400  
)

fig_pie.show()

heading2 = """               _   _ _                                              _ 
  _ _ ___ _ __| |_(_) |___ ___  _ _  ___ __ _ _ _   _  _ ___ _  _  (_)
 | '_/ -_) '_ \  _| | / -_|_-< | ' \/ -_) _` | '_| | || / _ \ || |  _ 
 |_| \___| .__/\__|_|_\___/__/ |_||_\___\__,_|_|    \_, \___/\_,_| (_)
         |_|                                        |__/              """

print(heading2)
print(divider)
print()

if len(unique_animals_df) == 0:
    first_sentence = "There are no animals nearby.\n"
elif len(unique_animals_df) == 1:
    first_sentence = f"There is a {unique_animals_df.iloc[0]['animalname']}s nearby.\n"
else:
    first_sentence = "There are "
    for i in range(len(unique_animals_df)):
        if i == len(unique_animals_df) - 1:
            first_sentence += f"and {unique_animals_df.iloc[i]['animalname']}s nearby.\n"
        else:
            first_sentence += f"{unique_animals_df.iloc[i]['animalname']}, "
    print(first_sentence)

for index, row in unique_animals_df.iterrows():
    if row['dangerous'] == 't':
        danger_sentence = "They are dangerous, so keep your distance and stay safe."
    else:
        danger_sentence = ""

    second_sentence = (
        f"The {row['animalname']} is {row['color']} in color and can grow up to "
        f"{row['size']} centimeters long.\nThey are active {row['active']}. {row['fact']}\n{danger_sentence}"
    )
    print(second_sentence)
    
fig.show()

  _____            _   _ _        _____           _            
 |  __ \          | | (_) |      |  __ \         | |           
 | |__) |___ _ __ | |_ _| | ___  | |__) |__ _  __| | __ _ _ __ 
 |  _  // _ \ '_ \| __| | |/ _ \ |  _  // _` |/ _` |/ _` | '__|
 | | \ \  __/ |_) | |_| | |  __/ | | \ \ (_| | (_| | (_| | |   
 |_|  \_\___| .__/ \__|_|_|\___| |_|  \_\__,_|\__,_|\__,_|_|   
            | |                                                
            |_|                                                
_________________________________________________________________________

Number of nearby sightings: 72

There are 6 reptiles near major roadways near you.
That is 8.33% of all sightings near you. Be mindful of their habitat.



               _   _ _                                              _ 
  _ _ ___ _ __| |_(_) |___ ___  _ _  ___ __ _ _ _   _  _ ___ _  _  (_)
 | '_/ -_) '_ \  _| | / -_|_-< | ' \/ -_) _` | '_| | || / _ \ || |  _ 
 |_| \___| .__/\__|_|_\___/__/ |_||_\___\__,_|_|    \_, \___/\_,_| (_)
         |_|                                        |__/              
_________________________________________________________________________

There are Rat Snake, Garter Snake, Red-Eared Sliders, and Snapping Turtles nearby.

The Rat Snake is black and white in color and can grow up to 91-152.4 centimeters long.
They are active during the day time. They are exceptionally good at climbing trees.

The Garter Snake is brown with a yellow stripe down their back in color and can grow up to 51-76.2 centimeters long.
They are active during the day time. From birth they are able to hunt by themselves.

The Red-Eared Sliders is green and red in color and can grow up to 12.7-20.32 centimeters long.
They are activ